## Implementando visualização dos dados em mapa
Com a biblioteca *folium* iremos criar uma visualização de mapa da cidade do Recife com suas divisões de bairros.

In [10]:
import pandas as pd
import numpy as np
import folium
from branca.colormap import linear

In [4]:
import json
#lembrar de trocar o caminho
with open('data/bairros2.json', 'r', encoding='utf-8-sig') as f:
   maprecife = json.load(f)
maprecife['features'][0]

{'type': 'Feature',
 'id': 0,
 'properties': {'bairro_codigo': 728,
  'bairro_nome_ca': 'CIDADE UNIVERSITARIA',
  'rpa': 4,
  'microrregiao': 3,
  'bairro_nome': 'Cidade Universitária'},
 'geometry': {'type': 'Polygon',
  'coordinates': [[[-34.944159036934906, -8.04984630501871],
    [-34.94419151990481, -8.050204895163283],
    [-34.94419743895523, -8.05027023442114],
    [-34.94431120757218, -8.051585950694623],
    [-34.94431131783154, -8.051594802624184],
    [-34.944311753991926, -8.051629758340791],
    [-34.942945018203595, -8.052009873555523],
    [-34.94315216357978, -8.053576771888464],
    [-34.94315812584044, -8.053621878336617],
    [-34.94601997813883, -8.052832348362527],
    [-34.94621711962542, -8.052791992945341],
    [-34.94623791711754, -8.052970794599196],
    [-34.946288170803314, -8.053987267004896],
    [-34.946298521226566, -8.054476939951423],
    [-34.94632422012583, -8.055943328908358],
    [-34.94632512171348, -8.056691220208132],
    [-34.946311149176296, 

In [5]:
#Latitude: -8.05428, Longitude: -34.8813
recifediv = folium.Map(location=[-8.05428, -34.8813],tiles='OpenStreetMap', zoom_start=12)
folium.GeoJson(
    maprecife
).add_to(recifediv)
recifediv

In [8]:
bairros_df = pd.read_csv('data/Bairro/bairro.csv', sep=',').dropna(how='all', axis = 1)
bairros_df.loc[93] = [93, 'PAU FERRO', 0]
bairros_df.head()

Unnamed: 0 no_bairro_residencia  quantidade
0           0               VARZEA         948
1           1                COHAB         911
2           2             IPUTINGA         718
3           3            AGUA FRIA         430
4           4             AFOGADOS         399

In [11]:
colormap_bairros = linear.YlOrRd_09.scale(
    bairros_df.quantidade.min(),
    bairros_df.quantidade.max())
colormap_bairros

In [12]:
bairrosCasos = bairros_df.set_index('no_bairro_residencia')['quantidade']

In [14]:
#casos de dengue classica
dengue_classica = pd.read_csv('data/Bairro/bairro_dengue.csv', sep=',')
dengue_classica.loc[93] = [93, 'PAU FERRO', 0]
dengue_classica.head()

Unnamed: 0 nome_logradouro_residencia  no_bairro_residencia
0           0                     VARZEA                   946
1           1                      COHAB                   904
2           2                   IPUTINGA                   718
3           3                  AGUA FRIA                   429
4           4                   AFOGADOS                   398

In [15]:
colormap_dengueclassica = linear.PuRd_09.scale(
    dengue_classica.no_bairro_residencia.min(),
    dengue_classica.no_bairro_residencia.max())
colormap_dengueclassica

In [16]:
classica = dengue_classica.set_index('nome_logradouro_residencia')['no_bairro_residencia']

In [17]:
#bairro_dengue_alarme: Dengue com sinais de alarme
dengue_alarme = pd.read_csv('data/Bairro/bairro_dengue_alarme.csv', sep=',')
dengue_alarme.head()

Unnamed: 0 nome_logradouro_residencia  quantidade
0           0                     VARZEA           0
1           1                      COHAB           7
2           2                   IPUTINGA           0
3           3                  AGUA FRIA           0
4           4                   AFOGADOS           1

In [18]:
colormap_alarme = linear.PuRd_09.scale(
    dengue_alarme.quantidade.min(),
    dengue_alarme.quantidade.max())
colormap_alarme

In [19]:
alarme = dengue_alarme.set_index('nome_logradouro_residencia')['quantidade']

In [20]:
#bairro_dengue_complicações: Dengue com sinais de complicações
dengue_complicacoes = pd.read_csv('data/Bairro/bairro_dengue_complicacoes.csv', sep=',')
dengue_complicacoes.head()

Unnamed: 0 nome_logradouro_residencia  quantidade
0           0                     VARZEA           2
1           1                      COHAB           0
2           2                   IPUTINGA           0
3           3                  AGUA FRIA           1
4           4                   AFOGADOS           0

In [21]:
colormap_complicacoes = linear.PuRd_09.scale(
    dengue_complicacoes.quantidade.min(),
    dengue_complicacoes.quantidade.max())
colormap_complicacoes

In [22]:
complicacoes = dengue_complicacoes.set_index('nome_logradouro_residencia')['quantidade']

In [23]:
#dengue com sinais graves
dengue_grave = pd.read_csv('data/Bairro/bairro_dengue_grave.csv', sep=',')
dengue_grave.head()

Unnamed: 0 nome_logradouro_residencia  quantidade
0           0                     VARZEA           0
1           1                      COHAB           0
2           2                   IPUTINGA           0
3           3                  AGUA FRIA           0
4           4                   AFOGADOS           0

In [24]:
colormap_grave = linear.PuRd_09.scale(
    dengue_grave.quantidade.min(),
    dengue_grave.quantidade.max())
colormap_grave

In [25]:
grave = dengue_grave.set_index('nome_logradouro_residencia')['quantidade']

In [26]:
recife = folium.Map(location=[-8.05428, -34.8813],tiles='OpenStreetMap', zoom_start=12)
#casos de dengue em geral
folium.GeoJson(maprecife, name='Dengue por Bairros',
    style_function=lambda feature: {
        'fillColor': colormap_bairros(bairrosCasos[feature['properties']['bairro_nome_ca']]),
        'color': 'black',
        'weight': 1,
        'dashArray': '5, 5',
        'fillOpacity': 0.8,
    }
).add_to(recife)
#colormap_bairros.caption = 'Casos de dengue por bairros em Recife'
#colormap_bairros.add_to(recife)
#dengue classica

folium.GeoJson(maprecife, name = 'Dengue Clássica', style_function=lambda feature: {
            'fillColor': colormap_dengueclassica(classica[feature['properties']['bairro_nome_ca']]),
            'color': 'black',
            'weight': 1,
            'dashArray': '5, 5',
            'fillOpacity': 0.8,
}).add_to(recife)
#colormap_dengueclassica.caption = "Casos de dengue clássica"
#colormap_dengueclassica.add_to(recife)
#dengue com sinais de alarme
folium.GeoJson(maprecife, name = 'Dengue com sinais de alarme', style_function=lambda feature: {
            'fillColor': colormap_alarme(alarme[feature['properties']['bairro_nome_ca']]),
            'color': 'black',
            'weight': 1,
            'dashArray': '5, 5',
            'fillOpacity': 0.8,
}).add_to(recife)
#colormap_alarme.caption = "Casos de dengue com sinais de alarme"
#colormap_alarme.add_to(recife)
#dengue com sinais de complicações
folium.GeoJson(maprecife, name = 'Dengue com sinais de complicações', style_function=lambda feature: {
            'fillColor': colormap_complicacoes(complicacoes[feature['properties']['bairro_nome_ca']]),
            'color': 'black',
            'weight': 1,
            'dashArray': '5, 5',
            'fillOpacity': 0.8,
}).add_to(recife)
#colormap_complicacoes.caption = "Casos de dengue com complicações"
#colormap_complicacoes.add_to(recife)
#dengue com sinais graves
folium.GeoJson(maprecife, name = 'Dengue com sinais graves', style_function=lambda feature: {
            'fillColor': colormap_grave(grave[feature['properties']['bairro_nome_ca']]),
            'color': 'black',
            'weight': 1,
            'dashArray': '5, 5',
            'fillOpacity': 0.8,
}).add_to(recife)
colormap_grave.caption = "Casos de dengue grave"
colormap_grave.add_to(recife)

folium.LayerControl().add_to(recife)
recife.save("index.html")
recife